## Automatically creating new binhost directories when profile or gcc version changes

On Gentoo Linux packages are compiled which is a time and energy consuming.
To minimise both, I have a binhost to share compiled binaries between devices.
The issues occurs when gcc major version changes - or a profile bump happens.
If I do not notice either - problem. Binaries might not be compatible.
So I wanted to automate a process of detection of those changes and automatically create subfolder for new binaries.
When investigating I learned a neat trick. For the wise ones this is trivial, for me it was enligtening.
Here it comes.

On a regular system, emerge resides here:

In [ ]:
$ which emerge
/usr/bin/emerge

On my box with binhost:

In [ ]:
$ which emerge
/usr/local/bin/emerge

And here is $PATH:

In [ ]:
$ echo $PATH
/usr/local/sbin:/usr/local/bin:/usr/bin:/opt/bin:/usr/lib/llvm/18/bin:/usr/lib/llvm/17/bin

So we see that on binhost box, there is emerge that resides in location preceeding regular emerge - so it gets called first.
It contains a shell script as follows:

In [ ]:
#!/usr/bin/env bash
#
# Script checking that binhost path exists before running emerge and
# creating it if not exists

PROFILE=$(eselect profile show|sed -n 2p|cut -d '/' -f4)
GCC_VERSION=$(eselect gcc show|cut -d '-' -f5)
BINHOST_DIR="/var/cache/binpkgs/${PROFILE}/gcc-${GCC_VERSION}.x/armv8a"

if [ ! -d "${BINHOST_DIR}" ]; then
        echo "${BINHOST_DIR} does not exist, creating"
        mkdir -p "${BINHOST_DIR}"
else echo "Binhost directory ${BINHOST_DIR} exists, proceeding with emerge ..."
fi

PKGDIR="${BINHOST_DIR}" /usr/bin/emerge "$@"

So on every profile change subfolder to /var/cache/binpkgs gets created,
on every gcc major version change, subfolder to /var/cache/binpkgs/<profile> gets created.
If folder already exists script only prints a message.
Then it calls /usr/bin/emerge - the regular emerge - with $PKGDIR variable, so binary packages are saved to the correct directory. 

This is structure of /var/cache/binpkgs:

In [ ]:
$ tree -L 3 /var/cache/binpkgs/
/var/cache/binpkgs/
├── 17.0
│   └── gcc-13.x
│       └── armv8a
└── 23.0
    ├── gcc-13.x
    │   └── armv8a
    └── gcc-14.x
        └── armv8a

One less thing to worry about.